# Identifying potential rice cultivation areas in Sierra Leone

* **Products used:**
[wofs_ls](https://explorer.digitalearth.africa/wofs_ls), 

### Background



### Description



## Getting started
**To run this analysis**, run all the cells in the notebook, starting with the "Load packages" cell.
***

### Load packages

In [1]:
import datacube
import numpy as np
import pandas as pd
import geopandas as gpd
import xarray as xr
import matplotlib.pyplot as plt

from datacube.utils import geometry
from datacube.utils.geometry import Geometry, CRS
from deafrica_tools.spatial import xr_rasterize
from deafrica_tools.plotting import map_shapefile
from deafrica_tools.dask import create_local_dask_cluster
from datacube.utils.cog import write_cog

import warnings
warnings.filterwarnings("ignore")

In [2]:
create_local_dask_cluster()

<Client: 'tcp://127.0.0.1:37385' processes=1 threads=4, memory=28.14 GB>

In [3]:
dc = datacube.Datacube(app='rice_potential')

## Analysis parameters

The following cell sets important parameters for the analysis:

* `shp_path`: a location path to the vector file (e.g. `folder/input.shp`). 

In [4]:
shp_path = 'data/sierra_leone_admin.geojson'

### Load shapefile

In [5]:
gdf = gpd.read_file(shp_path)

In [6]:
gdf.explore(column='ADM2_NAME')

In [7]:
query = {'resolution': (-30, 30),
         'output_crs': 'epsg:6933',
         'dask_chunks': dict(x=1000,y=1000)
         }

## Loop through regions

The cell below loops through the polygons and performs the following:
1. Load crop mask and restrict the output to each polygon (admin area).
2. Load WOfS, as per 1.
3. Define wetland based on WOfS frequency.
4. Define the 'current rice' area as pixels that are both wetlands and identified as crops by the crop mask.
5. Define the 'potential rice area' as pixels that are wetlands and are **not** identified as crops by the crop mask.
6. Write .tifs for each region to the results folder for later inspection.
7. Calculate each area and store.

In [8]:
wetlands = []
rice=[]
new_rice = []

# Loop through polygons in geodataframe and wofs and cropmask
i = 0
for index, row in gdf.iterrows():

    print(" Feature {:04}/{:04}\r".format(i + 1, len(gdf)), end="")

    # Extract the feature's geometry as a datacube geometry object
    geom = Geometry(geom=row.geometry, crs=gdf.crs)

    # Update the query to include our geopolygon
    query.update({'geopolygon': geom})

    # Load landsat
    cm = dc.load(product='crop_mask_western',
                 measurements='mask',**query).squeeze()

    # Generate a polygon mask to keep only data within the polygon
    mask = xr_rasterize(gdf.iloc[[index]], cm)

    # Mask dataset to set pixels outside the polygon to `NaN`
    cm = cm.where(mask)
    
    # Load WOfS
    wofs = dc.load(product='wofs_ls_summary_alltime',
                   measurements = 'frequency', **query).squeeze()

    # Generate a polygon mask to keep only data within the polygon
    wofs = wofs.where(mask)
    
    # total wetland area (including cultivated areas)
    wetland = (wofs.frequency < 0.75) & (wofs.frequency > 0.01)
    
    # current rice (where wetland = 1 and cm = 1)
    current_rice = xr.ufuncs.logical_and(wetland, cm.mask)
    
    # potential rice (where wetland and not currently rice)
    potential_rice = (wetland.astype(np.int8) - current_rice.astype(np.int8))
    
    # write to tifs for further inspection
    write_cog(wetland.astype(np.int8), fname=f'results/wetland{gdf.ADM2_NAME[i]}.tif', overwrite=True).compute()
    write_cog(current_rice.astype(np.int8), fname=f'results/current_rice{gdf.ADM2_NAME[i]}.tif', overwrite=True).compute()
    write_cog(potential_rice.astype(np.int8), fname=f'results/potential_rice{gdf.ADM2_NAME[i]}.tif', overwrite=True).compute()
    
    # area calculations
    area_per_pixel = query["resolution"][1]**2 / 1000**2
     
    new_rice.append((potential_rice.sum(dim=['x', 'y']) * area_per_pixel).compute().values.item())
    rice.append((current_rice.sum(dim=['x', 'y']) * area_per_pixel).compute().values.item())
    wetlands.append((wetland.sum(dim=['x', 'y']) * area_per_pixel).compute().values.item())
    
    i += 1

# Add results to geopandas gdf
gdf['Potential Rice Cultivation Area (km2)'] = new_rice
gdf['Current Rice Cultivation Area (km2)'] = rice
gdf['Total Wetland Area (including cultivated) (km2)'] = wetlands

### Save results

In [9]:
gdf = gdf.drop(['ISO3', 'ADM0_NAME', 'ENGTYPE0', 'ADM1_NAME', 'TYPE1', 'ENGTYPE1', 'TYPE2', 'ENGTYPE2', 'SOURCE_DT', 'SOURCE', 'SOURCE2_DT',
       'SOURCE2', 'GLOBALID', 'SHAPE_Leng', 'SHAPE_Area'], axis=1)

In [10]:
gdf.to_file('results/Sierra_Leone_rice_cultivation_area.shp')

## Plot results

### Potential Rice Cultivation areas

In [11]:
gdf.explore(column='Potential Rice Cultivation Area (km2)', vmin=0, vmax=400)

### Current Rice Cultivation Area

In [12]:
gdf.explore(column='Current Rice Cultivation Area (km2)', vmin=0, vmax=400)

### Total Wetland area

In [13]:
gdf.explore(column='Total Wetland Area (including cultivated) (km2)', vmin=0, vmax=400)

***

## Additional information

**License:** The code in this notebook is licensed under the [Apache License, Version 2.0](https://www.apache.org/licenses/LICENSE-2.0). 
Digital Earth Africa data is licensed under the [Creative Commons by Attribution 4.0](https://creativecommons.org/licenses/by/4.0/) license.

**Contact:** If you need assistance, please post a question on the [Open Data Cube Slack channel](http://slack.opendatacube.org/) or on the [GIS Stack Exchange](https://gis.stackexchange.com/questions/ask?tags=open-data-cube) using the `open-data-cube` tag (you can view previously asked questions [here](https://gis.stackexchange.com/questions/tagged/open-data-cube)).
If you would like to report an issue with this notebook, you can file one on [Github](https://github.com/digitalearthafrica/deafrica-sandbox-notebooks).

**Last modified:** Feb 2020

**Compatible `datacube` version:** 

In [14]:
print(datacube.__version__)

1.8.6
